In [1]:
from functools import cache
import pandas as pd

pd.set_option("display.max_columns", None)

In [2]:
estados_mexicanos = {
    "AGUASCALIENTES",
    "BAJA CALIFORNIA",
    "BAJA CALIFORNIA SUR",
    "CAMPECHE",
    "CHIAPAS",
    "CHIHUAHUA",
    "COAHUILA DE ZARAGOZA",
    "COLIMA",
    "DISTRITO FEDERAL",
    "DURANGO",
    "GUANAJUATO",
    "GUERRERO",
    "HIDALGO",
    "JALISCO",
    "MEXICO",
    "MICHOACAN DE OCAMPO",
    "MORELOS",
    "NAYARIT",
    "NUEVO LEON",
    "OAXACA",
    "PUEBLA",
    "QUERETARO  DE ARTEAGA",
    "QUINTANA ROO",
    "SAN LUIS POTOSI",
    "SINALOA",
    "SONORA",
    "TABASCO",
    "TAMAULIPAS",
    "TLAXCALA",
    "VERACRUZ DE IGNACIO DE LA LLAVE",
    "YUCATAN",
    "ZACATECAS",
}

In [3]:
df = pd.read_csv("2010-2019.csv")

/var/folders/05/y38rqjl55hjb_hbnypxzgrsw0000gn/T/ipykernel_93495/3168623387.py:1: DtypeWarning: Columns (21) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("2010-2019.csv")


In [4]:
def _ano_nacimiento_vivo_func(str_date):
    try:
        return str_date.split("/")[-1]
    except:
        return ""


df["año_de_nacimiento_vivo"] = df["fecha_nacimiento_nac_vivo"].apply(
    _ano_nacimiento_vivo_func
)

In [19]:
df = df[(5 < df["edad_madre"]) & (df["edad_madre"] < 90)]

In [20]:
df_trisomias = df[df["codigo_anomalia"].apply(lambda x: "Q9" in str(x))]

In [21]:
consulta_trisomias = df_trisomias.groupby(["año_de_nacimiento_vivo"]).agg(
    {
        "edad_madre": [
            "count",
            "mean",
            "std",
            "min",
            "max",
        ],
    }
)
consulta_trisomias

edad_madre                             
                            count       mean       std min max
año_de_nacimiento_vivo                                        
2010                          930  30.546237  8.244939  10  48
2011                         1051  31.010466  8.193777  12  49
2012                          961  30.462019  8.310565  13  47
2013                         1055  31.182938  8.247919  11  51
2014                         1031  31.018429  8.356304  13  50
2015                         1016  31.500984  8.295052  14  52
2016                         1044  31.453065  8.147413  14  47
2017                         1043  31.410355  8.174581  13  47
2018                         1059  31.064212  8.173198  13  48
2019                          941  32.018066  8.195918  13  47

In [22]:
# Edades de madres
consulta_total = df.groupby(["año_de_nacimiento_vivo"]).agg(
    {
        "edad_madre": [
            "count",
            "mean",
            "std",
            "min",
            "max",
        ],
    }
)
consulta_total

edad_madre                             
                            count       mean       std min max
año_de_nacimiento_vivo                                        
2010                      2063533  25.253220  6.319567   9  58
2011                      2156751  25.234223  6.331894   9  58
2012                      2197327  25.195768  6.321840   9  58
2013                      2189257  25.198235  6.322081   9  59
2014                      2173773  25.276009  6.322130   9  58
2015                      2143345  25.367835  6.296604   9  59
2016                      2079251  25.468008  6.292815   9  59
2017                      2037647  25.510821  6.305873   9  62
2018                      1940338  25.678051  6.328369   9  60
2019                      1867693  25.840630  6.342544   9  58

In [23]:
consulta = consulta_total.join(
    consulta_trisomias, rsuffix="_trisomias", lsuffix="_general"
)

In [24]:
consulta["porcentaje"] = (
    consulta[("edad_madre_trisomias", "count")]
    / consulta[("edad_madre_general", "count")]
)

In [25]:
consulta

edad_madre_general                               \
                                    count       mean       std min max   
año_de_nacimiento_vivo                                                   
2010                              2063533  25.253220  6.319567   9  58   
2011                              2156751  25.234223  6.331894   9  58   
2012                              2197327  25.195768  6.321840   9  58   
2013                              2189257  25.198235  6.322081   9  59   
2014                              2173773  25.276009  6.322130   9  58   
2015                              2143345  25.367835  6.296604   9  59   
2016                              2079251  25.468008  6.292815   9  59   
2017                              2037647  25.510821  6.305873   9  62   
2018                              1940338  25.678051  6.328369   9  60   
2019                              1867693  25.840630  6.342544   9  58   

                       edad_madre_trisomias                               \
                                      count       mean       std min max   
año_de_nacimiento_vivo                                                     
2010                                    930  30.546237  8.244939  10  48   
2011                                   1051  31.010466  8.193777  12  49   
2012                                    961  30.462019  8.310565  13  47   
2013                                   1055  31.182938  8.247919  11  51   
2014                                   1031  31.018429  8.356304  13  50   
2015                                   1016  31.500984  8.295052  14  52   
2016                                   1044  31.453065  8.147413  14  47   
2017                                   1043  31.410355  8.174581  13  47   
2018                                   1059  31.064212  8.173198  13  48   
2019                                    941  32.018066  8.195918  13  47   

                       porcentaje  
                                   
año_de_nacimiento_vivo             
2010                     0.000451  
2011                     0.000487  
2012                     0.000437  
2013                     0.000482  
2014                     0.000474  
2015                     0.000474  
2016                     0.000502  
2017                     0.000512  
2018                     0.000546  
2019                     0.000504

# Pendiente

Generar gráfica de cajas con edades de las madres con hijos de trisomias.

https://stackoverflow.com/a/66565512